In [1]:
import json
import glob
import os
import pandas as pd
import numpy as np
from skimage.external import tifffile
from IPython.display import clear_output
from scipy.stats import wasserstein_distance
from skimage import img_as_float

In [2]:
def mkdirp(directory):
    if not os.path.exists(directory):
        os.makedirs(directory)

In [3]:
mkdirp("analysis/deconv")

In [4]:
def compare_images(img0, img1):   
    img0 -= np.mean(img0)
    img1 -= np.mean(img1)
    img0 /= np.std(img0)
    img1 /= np.std(img1)
    return np.sum(np.abs(img0 - img1)) / np.prod(np.array(img0.shape))
    #return np.abs(np.mean(img0) - np.mean(img1))

In [5]:
def standardized(img):
    img -= np.mean(img)
    img /= np.std(img)
    return img

In [6]:
def compare_images_wasserstein(img0, img1):      
    return wasserstein_distance(img0.flatten(), img1.flatten())

In [7]:
def images_are_equal(img0, img1):   
    df = np.abs(img0 - img1)
    return np.all(df < 1e-09)

In [8]:
def images_are_equal_wasserstein(img0, img1):      
    return compare_images_wasserstein(img0, img1) < 1e-09

In [9]:
def compare_tiffs(img0_path, img1_path, f=compare_images):
    return f(tifffile.imread(img0_path), tifffile.imread(img1_path))

In [10]:
def get_deconvolved_tiff(run_path, sample):
    if "misaxx" in run_path:
        return run_path + "/output-docker/" + sample + "/deconvolved/data.tif"
    else:
        return run_path + "/output/" + sample + "/deconvolved.tif"

In [11]:
def get_original_tiff(sample):
    return "/data/rgerst_data/Af_labelledSpore_DiDlabelledMHS/input-deconv/" + sample + "/in/data.tif"

# Deconvolution score via Wasserstein distance

* Score each deconvolution by Wasserstein
* Save score as output
* Score distributions should be the same across samples

In [17]:
samples = [os.path.basename(x) for x in glob.glob("deconv_python_snakemake_dag30_optMT/output/*")]
df = pd.DataFrame(index=samples)

for run_path in ["deconv_cxx_misaxx_dag30_optMT", "deconv_java_deconvlab2_dag30_noopMT", "deconv_python_snakemake_dag30_optMT"]:
    run = os.path.basename(run_path)
    distances = []
    
    for sample in samples:
        clear_output()
        print(sample, run)
        # We remove the border, as FFT artifacts disturb the distributions
        img_deconv = standardized(img_as_float(tifffile.imread(get_deconvolved_tiff(run_path, sample))[32:-32,32:-32]))
        img_original = standardized(img_as_float(tifffile.imread(get_original_tiff(sample))[32:-32,32:-32]))
        distance = compare_images_wasserstein(img_original, img_deconv)
        distances.append(distance)
    
    df[run] = distances
    
df.to_csv("analysis/deconv/wasserstein_distances.csv")

ATTC_1µL_DID_1stReplicate-Experiment-5304 deconv_python_snakemake_dag30_optMT


# Runtimes

In [12]:
def read_python_runtime(directory):
    with open(directory + "/runtime.log", "r") as f:
        return float(f.read()) / 60
    
def read_java_runtime(directory):
    with open(directory + "/output/runtime.log", "r") as f:
        return float(f.read()) / 1000 / 60
    
def read_misaxx_runtime(directory):
    json_data = None
    with open(directory + "/output-docker/runtime-log.json", "r") as f:
        json_data = json.load(f)
    thread0_data = json_data["entries"]["thread0"]
    end_times = [x["end-time"] for x in thread0_data]
    return np.max(end_times) / 1000 / 60

In [13]:
runtime_runs = []
runtime_runtimes = []

for run_path in glob.glob("./deconv_python*"):
    if not os.path.isdir(run_path):
        continue
    run = os.path.basename(run_path)
    rt = read_python_runtime(run_path)
    runtime_runs.append(run)
    runtime_runtimes.append(rt)
    
for run_path in glob.glob("./deconv_java*"):
    if not os.path.isdir(run_path):
        continue
    run = os.path.basename(run_path)
    rt = read_java_runtime(run_path)
    runtime_runs.append(run)
    runtime_runtimes.append(rt)  
    
for run_path in glob.glob("./deconv_cxx*"):
    if not os.path.isdir(run_path):
        continue
    run = os.path.basename(run_path)
    rt = read_misaxx_runtime(run_path)
    runtime_runs.append(run)
    runtime_runtimes.append(rt)

df_runtime = pd.DataFrame({"Runtime (min)": runtime_runtimes}, index=runtime_runs)

In [14]:
df_runtime

Runtime (min)
deconv_python_snakemake_dag30_nooptMT       1.450000
deconv_python_snakemake_dag30_optMT         0.883333
deconv_python_snakemake_noMT_optMT         18.500000
deconv_python_snakemake_noMT_nooptMT       18.083333
deconv_java_deconvlab2_dag30_noopMT         3.186833
deconv_java_deconvlab2_noMT_noopMT         11.800350
deconv_cxx_misaxx_dag30_nooptMT             0.156235
deconv_cxx_misaxx_noMT_optMT                2.998074
deconv_cxx_misaxx_dag30_optMT               0.155073
deconv_cxx_misaxx_noMT_nooptMT              2.822988

In [11]:
df_runtime.to_csv("analysis/deconv/runtimes.csv")

# Intra-implementation equality

In [16]:
for implementation in ["cxx", "java", "python"]:
    for sample_ in glob.glob("deconv_python_snakemake_dag30_optMT/output/*"):
        sample = os.path.basename(sample_)

        run_paths = glob.glob("deconv_" + implementation + "_*")
        run_paths = [x for x in run_paths if os.path.isdir(x)]
        runs = [os.path.basename(x) for x in run_paths]

        for i in range(len(run_paths)):
            for j in range(i, len(run_paths)):
                clear_output()
                print(implementation, sample, (i, j), len(run_paths))

                eq = compare_tiffs(get_deconvolved_tiff(run_paths[i], sample), get_deconvolved_tiff(run_paths[j], sample), f=images_are_equal_wasserstein)
                assert eq

python ATTC_1µL_DID_1stReplicate-Experiment-5304 (3, 3) 4
